# A full business solution

Let's assume I publish a weekly oline newletter every week where I talk about one organization and one famous personality. 

I am going to create a program to quickly summarize information about an organization or a person and publish my newsletter.

Just to be fancy, I will also show you how we can publish in a streaming fashion in this notebook! But you'll have to run this notebook for the streaming experience. :) 

In [1]:
import os
import requests
import json
from typing import List
from dotenv import load_dotenv
from bs4 import BeautifulSoup
from IPython.display import Markdown, display, update_display
from openai import OpenAI

In [2]:
#This week in my newsletter I am showcasing summarizing OpenAI and MerylStreep!
open_ai_wiki_url = "https://en.wikipedia.org/wiki/OpenAI"
meryl_wiki_url = "https://en.wikipedia.org/wiki/Meryl_Streep"

In [3]:
# Initialize and constants

load_dotenv(override=True)
api_key = os.getenv('OPENAI_API_KEY')

if api_key and api_key.startswith('sk-proj-') and len(api_key)>10:
    print("API key looks good so far")
else:
    print("There might be a problem with your API key? Please visit the troubleshooting notebook!")
    
MODEL = 'gpt-4o-mini'
openai = OpenAI()

API key looks good so far


In [4]:
# A class to represent a Webpage

# Some websites need you to use proper headers when fetching them:
headers = {
 "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/117.0.0.0 Safari/537.36"
}

class Website:
    """
    A utility class to represent a Website that we have scraped, now with links
    """

    def __init__(self, url):
        self.url = url
        response = requests.get(url, headers=headers)
        self.body = response.content
        soup = BeautifulSoup(self.body, 'html.parser')
        self.title = soup.title.string if soup.title else "No title found"
        if soup.body:
            for irrelevant in soup.body(["script", "style", "img", "input"]):
                irrelevant.decompose()
            self.text = soup.body.get_text(separator="\n", strip=True)
        else:
            self.text = ""
        links = [link.get('href') for link in soup.find_all('a')]
        self.links = [link for link in links if link]

    def get_contents(self):
        return f"Webpage Title:\n{self.title}\nWebpage Contents:\n{self.text}\n\n"

In [5]:
wiki_openai = Website(open_ai_wiki_url)
wiki_openai.links

['#bodyContent',
 '/wiki/Main_Page',
 '/wiki/Wikipedia:Contents',
 '/wiki/Portal:Current_events',
 '/wiki/Special:Random',
 '/wiki/Wikipedia:About',
 '//en.wikipedia.org/wiki/Wikipedia:Contact_us',
 '/wiki/Help:Contents',
 '/wiki/Help:Introduction',
 '/wiki/Wikipedia:Community_portal',
 '/wiki/Special:RecentChanges',
 '/wiki/Wikipedia:File_upload_wizard',
 '/wiki/Special:SpecialPages',
 '/wiki/Main_Page',
 '/wiki/Special:Search',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=OpenAI',
 '/w/index.php?title=Special:UserLogin&returnto=OpenAI',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=OpenAI',
 '/w/index.php?title=Special:UserLogin&returnto=OpenAI',
 '/wiki/Help:Introduction',
 '/wiki/Special:MyContributions',
 '/wiki/Special:MyTalk',
 '#',
 '#History',


In [6]:
wiki_meryl = Website(meryl_wiki_url)
wiki_meryl.links

['#bodyContent',
 '/wiki/Main_Page',
 '/wiki/Wikipedia:Contents',
 '/wiki/Portal:Current_events',
 '/wiki/Special:Random',
 '/wiki/Wikipedia:About',
 '//en.wikipedia.org/wiki/Wikipedia:Contact_us',
 '/wiki/Help:Contents',
 '/wiki/Help:Introduction',
 '/wiki/Wikipedia:Community_portal',
 '/wiki/Special:RecentChanges',
 '/wiki/Wikipedia:File_upload_wizard',
 '/wiki/Special:SpecialPages',
 '/wiki/Main_Page',
 '/wiki/Special:Search',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=Meryl+Streep',
 '/w/index.php?title=Special:UserLogin&returnto=Meryl+Streep',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=Meryl+Streep',
 '/w/index.php?title=Special:UserLogin&returnto=Meryl+Streep',
 '/wiki/Help:Introduction',
 '/wiki/Special:MyContributions',
 '/wiki/Special:MyTa

## First step: Have GPT-4o-mini figure out which links are relevant

### Use a call to gpt-4o-mini to read the links on a webpage, and respond in structured JSON.  
It should decide which links are relevant, and replace relative links such as "/about" with "https://company.com/about".  
We will use "one shot prompting" in which we provide an example of how it should respond in the prompt.

This is an excellent use case for an LLM, because it requires nuanced understanding. Imagine trying to code this without LLMs by parsing and analyzing the webpage - it would be very hard!

Sidenote: there is a more advanced technique called "Structured Outputs" in which we require the model to respond according to a spec. We cover this technique in Week 8 during our autonomous Agentic AI project.

In [7]:
link_system_prompt = "You are provided with a list of links found on a wikipedia search result page. \
You are able to decide which of the links would be most relevant to include in a creative snapshot summary about the topic searched on wikipedia., \
such as links technical terms, important people listed in the wikipedia description, links to any historical references, books, movies, awards, etc,.\n"
link_system_prompt += "You should respond in JSON as in these examples:"
link_system_prompt += """
{
    "links": [
        {"type": "Founder & Key Persons - Sam Altman", "url": "https://full.url/goes/here/person1"},
        {"type": "Founder & Key Persons - Bret Taylor", "url": "https://full.url/goes/here/person2"},
        {"type": "Founder & Competitor - Elon Musk", "url": "https://another.full.url/person3"},
        {"type": "Products - GPT-5", "url": "https://another.full.url/product1"},
        {"type": "Products - DALL-E", "url": "https://another.full.url/product2"}
    ]
}
"""
link_system_prompt += """
{
    "links": [
        {"type": "University: Vassar College (AB)", "url": "https://full.url/goes/here/uni1"},
        {"type": "University: Yale University (MFA)", "url": "https://full.url/goes/here/uni2"},
        {"type": "Spouse - Don Gummer", "url": "https://another.full.url/person1"},
        {"type": "Partner - John Cazale", "url": "https://another.full.url/person2"},
        {"type": "Child: Henry", "url": "https://another.full.url/child1"},
        {"type": "Child: Mamie", "url": "https://another.full.url/child2"},
        {"type": "Child: Grace", "url": "https://another.full.url/child3"},
        {"type": "Child: Louisa", "url": "https://another.full.url/child4"},
        {"type": "film", "url": "https://another.full.url/child1"},
        {"type": "film", "url": "https://another.full.url/child1"},
        {"type": "Award: BAFTA", "url": "https://another.full.url/award1"},
        {"type": "Award: Tony", "url": "https://another.full.url/award2"},
        {"type": "Award: Emmy", "url": "https://another.full.url/award3"}
    ]
}
"""

In [8]:
print(link_system_prompt)

You are provided with a list of links found on a wikipedia search result page. You are able to decide which of the links would be most relevant to include in a creative snapshot summary about the topic searched on wikipedia., such as links technical terms, important people listed in the wikipedia description, links to any historical references, books, movies, awards, etc,.
You should respond in JSON as in these examples:
{
    "links": [
        {"type": "Founder & Key Persons - Sam Altman", "url": "https://full.url/goes/here/person1"},
        {"type": "Founder & Key Persons - Bret Taylor", "url": "https://full.url/goes/here/person2"},
        {"type": "Founder & Competitor - Elon Musk", "url": "https://another.full.url/person3"},
        {"type": "Products - GPT-5", "url": "https://another.full.url/product1"},
        {"type": "Products - DALL-E", "url": "https://another.full.url/product2"}
    ]
}

{
    "links": [
        {"type": "University: Vassar College (AB)", "url": "https://

In [9]:
def get_links_user_prompt(website):
    user_prompt = f"Here is the list of links on the website of {website.url} - "
    user_prompt += "please decide which of these are relevant web links for a brochure about the company, respond with the full https URL in JSON format. \
Do not include Terms of Service, Privacy, email links.\n"
    user_prompt += "Links (some might be relative links):\n"
    user_prompt += "\n".join(website.links)
    return user_prompt

In [10]:
print(get_links_user_prompt(wiki_openai))

Here is the list of links on the website of https://en.wikipedia.org/wiki/OpenAI - please decide which of these are relevant web links for a brochure about the company, respond with the full https URL in JSON format. Do not include Terms of Service, Privacy, email links.
Links (some might be relative links):
#bodyContent
/wiki/Main_Page
/wiki/Wikipedia:Contents
/wiki/Portal:Current_events
/wiki/Special:Random
/wiki/Wikipedia:About
//en.wikipedia.org/wiki/Wikipedia:Contact_us
/wiki/Help:Contents
/wiki/Help:Introduction
/wiki/Wikipedia:Community_portal
/wiki/Special:RecentChanges
/wiki/Wikipedia:File_upload_wizard
/wiki/Special:SpecialPages
/wiki/Main_Page
/wiki/Special:Search
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en
/w/index.php?title=Special:CreateAccount&returnto=OpenAI
/w/index.php?title=Special:UserLogin&returnto=OpenAI
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&u

In [11]:
print(get_links_user_prompt(wiki_meryl))

Here is the list of links on the website of https://en.wikipedia.org/wiki/Meryl_Streep - please decide which of these are relevant web links for a brochure about the company, respond with the full https URL in JSON format. Do not include Terms of Service, Privacy, email links.
Links (some might be relative links):
#bodyContent
/wiki/Main_Page
/wiki/Wikipedia:Contents
/wiki/Portal:Current_events
/wiki/Special:Random
/wiki/Wikipedia:About
//en.wikipedia.org/wiki/Wikipedia:Contact_us
/wiki/Help:Contents
/wiki/Help:Introduction
/wiki/Wikipedia:Community_portal
/wiki/Special:RecentChanges
/wiki/Wikipedia:File_upload_wizard
/wiki/Special:SpecialPages
/wiki/Main_Page
/wiki/Special:Search
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en
/w/index.php?title=Special:CreateAccount&returnto=Meryl+Streep
/w/index.php?title=Special:UserLogin&returnto=Meryl+Streep
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=

In [12]:
def get_links(url):
    website = Website(url)
    response = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": link_system_prompt},
            {"role": "user", "content": get_links_user_prompt(website)}
      ],
        response_format={"type": "json_object"}
    )
    result = response.choices[0].message.content
    return json.loads(result)

In [13]:
get_links(open_ai_wiki_url)

{'links': [{'type': 'Official Website', 'url': 'https://openai.com/'},
  {'type': 'History of OpenAI - 2015: founding and initial motivations',
   'url': 'https://en.wikipedia.org/wiki/OpenAI#2015:_founding_and_initial_motivations'},
  {'type': 'Key Person - Sam Altman',
   'url': 'https://en.wikipedia.org/wiki/Sam_Altman'},
  {'type': 'Key Person - Elon Musk',
   'url': 'https://en.wikipedia.org/wiki/Elon_Musk'},
  {'type': 'Key Person - Ilya Sutskever',
   'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'},
  {'type': 'Key Person - Greg Brockman',
   'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'},
  {'type': 'Key Person - Sarah Friar',
   'url': 'https://en.wikipedia.org/wiki/Sarah_Friar'},
  {'type': 'Key Person - Mira Murati',
   'url': 'https://en.wikipedia.org/wiki/Mira_Murati'},
  {'type': 'Key Person - Reid Hoffman',
   'url': 'https://en.wikipedia.org/wiki/Reid_Hoffman'},
  {'type': 'Key Product - ChatGPT',
   'url': 'https://en.wikipedia.org/wiki/ChatGPT'},
  {'typ

In [14]:
get_links(meryl_wiki_url)

{'links': [{'type': 'University: Vassar College',
   'url': 'https://en.wikipedia.org/wiki/Vassar_College'},
  {'type': 'University: Yale University',
   'url': 'https://en.wikipedia.org/wiki/Yale_University'},
  {'type': 'Spouse: Don Gummer',
   'url': 'https://en.wikipedia.org/wiki/Don_Gummer'},
  {'type': 'Partner: John Cazale',
   'url': 'https://en.wikipedia.org/wiki/John_Cazale'},
  {'type': 'Child: Henry Wolfe',
   'url': 'https://en.wikipedia.org/wiki/Henry_Wolfe'},
  {'type': 'Child: Mamie Gummer',
   'url': 'https://en.wikipedia.org/wiki/Mamie_Gummer'},
  {'type': 'Child: Grace Gummer',
   'url': 'https://en.wikipedia.org/wiki/Grace_Gummer'},
  {'type': 'Child: Louisa Jacobson',
   'url': 'https://en.wikipedia.org/wiki/Louisa_Jacobson'},
  {'type': 'List of awards and nominations received by Meryl Streep',
   'url': 'https://en.wikipedia.org/wiki/List_of_awards_and_nominations_received_by_Meryl_Streep'},
  {'type': 'Film: The Devil Wears Prada',
   'url': 'https://en.wikipedi

## Second step: make a summary page for my newsletter!

Assemble all the details into another prompt to GPT4-o, and also get information about the important aspects with in the organization or persona's wiki.

In [15]:
def get_all_details(url):
    result = "Landing page:\n"
    result += Website(url).get_contents()
    links = get_links(url)
    print("Found links:", links)
    for link in links["links"]:
        result += f"\n\n{link['type']}\n"
        result += Website(link["url"]).get_contents()
    return result

In [16]:
print(get_all_details(open_ai_wiki_url))

Found links: {'links': [{'type': 'Company Website', 'url': 'https://openai.com/'}, {'type': 'Founders - Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Founders - Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Founders - Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Key Person - Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Key Person - Mira Murati', 'url': 'https://en.wikipedia.org/wiki/Mira_Murati'}, {'type': 'Product - ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'Product - DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'Product - GPT-3', 'url': 'https://en.wikipedia.org/wiki/GPT-3'}, {'type': 'Product - GPT-4', 'url': 'https://en.wikipedia.org/wiki/GPT-4'}, {'type': 'Visual Art AI - DALL·E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'AI Research - OpenAI Codex', 'url': 'https://en.wikipedia.org/wiki/Ope

In [17]:
print(get_all_details(meryl_wiki_url))

Found links: {'links': [{'type': "Film: Sophie's Choice (1982)", 'url': 'https://en.wikipedia.org/wiki/Sophie%27s_Choice_(film)'}, {'type': 'Film: The Iron Lady (2011)', 'url': 'https://en.wikipedia.org/wiki/The_Iron_Lady_(film)'}, {'type': 'Film: Kramer vs. Kramer (1979)', 'url': 'https://en.wikipedia.org/wiki/Kramer_vs._Kramer'}, {'type': 'Film: Out of Africa (1985)', 'url': 'https://en.wikipedia.org/wiki/Out_of_Africa_(film)'}, {'type': 'Film: The Devil Wears Prada (2006)', 'url': 'https://en.wikipedia.org/wiki/The_Devil_Wears_Prada_(film)'}, {'type': 'Film: Julie & Julia (2009)', 'url': 'https://en.wikipedia.org/wiki/Julie_%26_Julia'}, {'type': 'Film: Florence Foster Jenkins (2016)', 'url': 'https://en.wikipedia.org/wiki/Florence_Foster_Jenkins_(film)'}, {'type': 'Film: Mamma Mia! (2008)', 'url': 'https://en.wikipedia.org/wiki/Mamma_Mia!_(film)'}, {'type': 'Film: Doubt (2008)', 'url': 'https://en.wikipedia.org/wiki/Doubt_(2008_film)'}, {'type': 'Film: August: Osage County (2013)', 

In [18]:
system_prompt = "You are the editor of a graduate student newsletter in a business school. Every week you write a piece on an organization and a famous persona \
in which you borrow and summarize contents from their wiki page. In fact you call your piece \"What does Wiki say!\".  In addition to summarizing their wikipedia page \
you also highlight relevance facts that relate to this org or person from the the contents of several relevant pages linked on the org or persona\'s page. \
and creates a short brochure about the company for prospective customers, investors and recruits. Respond in markdown.\
For an organization include details of founders, competitors, major products, funding or stock outlook, and future directions. For a person include their work, what made them \
who they are, import works, awards and recognitions, important life events both professions and personal, and info about important people in their lives. Oh an btw, \
you have a great sense of humor but that you whip out 15-20% of the times for maximum impact in your writing.  Respond in markdown."

In [19]:
def get_brochure_user_prompt(name, url):
    user_prompt = f"You are looking at the wikiepdia of a company or person called: {name}\n"
    user_prompt += f"Here are the contents of its their wiki page and other relevant pages; use this information to write a short newsletter article on them in markdown.\n"
    user_prompt += get_all_details(url)
    user_prompt = user_prompt[:5_000] # Truncate if more than 5,000 characters
    return user_prompt

In [20]:
get_brochure_user_prompt("OpenAI", open_ai_wiki_url)

Found links: {'links': [{'type': 'Official Website', 'url': 'https://openai.com/'}, {'type': 'Founders - Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Founders - Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Founders - Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Founders - Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Products - ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'Products - DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'Products - GPT-3', 'url': 'https://en.wikipedia.org/wiki/GPT-3'}, {'type': 'Products - GPT-4', 'url': 'https://en.wikipedia.org/wiki/GPT-4'}, {'type': 'Products - GPT-5', 'url': 'https://en.wikipedia.org/wiki/GPT-5'}, {'type': 'Corporate Structure', 'url': 'https://openai.com/our-structure'}, {'type': 'Artificial Intelligence', 'url': 'https://en.wikipedia.org/wiki/Artificial_intelligence'

'You are looking at the wikiepdia of a company or person called: OpenAI\nHere are the contents of its their wiki page and other relevant pages; use this information to write a short newsletter article on them in markdown.\nLanding page:\nWebpage Title:\nOpenAI - Wikipedia\nWebpage Contents:\nJump to content\nMain menu\nMain menu\nmove to sidebar\nhide\nNavigation\nMain page\nContents\nCurrent events\nRandom article\nAbout Wikipedia\nContact us\nContribute\nHelp\nLearn to edit\nCommunity portal\nRecent changes\nUpload file\nSpecial pages\nSearch\nSearch\nAppearance\nDonate\nCreate account\nLog in\nPersonal tools\nDonate\nCreate account\nLog in\nPages for logged out editors\nlearn more\nContributions\nTalk\nContents\nmove to sidebar\nhide\n(Top)\n1\nHistory\nToggle History subsection\n1.1\n2015: founding and initial motivations\n1.2\n2016–2018: Non-profit beginnings\n1.3\n2019: Transition from non-profit\n1.4\n2020–2023: ChatGPT, DALL-E, partnership with Microsoft\n1.5\n2024: Public/Non-

In [21]:
get_brochure_user_prompt("Meryl", meryl_wiki_url)

Found links: {'links': [{'type': 'University: Vassar College', 'url': 'https://en.wikipedia.org/wiki/Vassar_College'}, {'type': 'University: Yale University', 'url': 'https://en.wikipedia.org/wiki/Yale_University'}, {'type': 'Spouse - Don Gummer', 'url': 'https://en.wikipedia.org/wiki/Don_Gummer'}, {'type': 'Partner - John Cazale', 'url': 'https://en.wikipedia.org/wiki/John_Cazale'}, {'type': 'Child: Henry Wolfe', 'url': 'https://en.wikipedia.org/wiki/Henry_Wolfe'}, {'type': 'Child: Mamie Gummer', 'url': 'https://en.wikipedia.org/wiki/Mamie_Gummer'}, {'type': 'Child: Grace Gummer', 'url': 'https://en.wikipedia.org/wiki/Grace_Gummer'}, {'type': 'Child: Louisa Jacobson', 'url': 'https://en.wikipedia.org/wiki/Louisa_Jacobson'}, {'type': 'Acting credits and awards', 'url': 'https://en.wikipedia.org/wiki/List_of_awards_and_nominations_received_by_Meryl_Streep'}, {'type': 'Film: The Devil Wears Prada', 'url': 'https://en.wikipedia.org/wiki/The_Devil_Wears_Prada_(film)'}, {'type': 'Film: Mamm

'You are looking at the wikiepdia of a company or person called: Meryl\nHere are the contents of its their wiki page and other relevant pages; use this information to write a short newsletter article on them in markdown.\nLanding page:\nWebpage Title:\nMeryl Streep - Wikipedia\nWebpage Contents:\nJump to content\nMain menu\nMain menu\nmove to sidebar\nhide\nNavigation\nMain page\nContents\nCurrent events\nRandom article\nAbout Wikipedia\nContact us\nContribute\nHelp\nLearn to edit\nCommunity portal\nRecent changes\nUpload file\nSpecial pages\nSearch\nSearch\nAppearance\nDonate\nCreate account\nLog in\nPersonal tools\nDonate\nCreate account\nLog in\nPages for logged out editors\nlearn more\nContributions\nTalk\nContents\nmove to sidebar\nhide\n(Top)\n1\nEarly life and education\n2\nCareer\nToggle Career subsection\n2.1\n1970s: Early work and breakthrough\n2.2\n1980s: Rise to prominence\n2.3\n1990s: Commercial fluctuations\n2.4\n2000s: Career resurgence and stage work\n2.5\n2010s: Furthe

In [22]:
def create_brochure(name, url):
    response = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": get_brochure_user_prompt(name, url)}
          ],
    )
    result = response.choices[0].message.content
    display(Markdown(result))

In [23]:
create_brochure("OpenAI", open_ai_wiki_url)

Found links: {'links': [{'type': 'History of OpenAI', 'url': 'https://en.wikipedia.org/wiki/OpenAI#History'}, {'type': '2015: founding and initial motivations', 'url': 'https://en.wikipedia.org/wiki/OpenAI#2015:_founding_and_initial_motivations'}, {'type': '2020–2023: ChatGPT, DALL-E, partnership with Microsoft', 'url': 'https://en.wikipedia.org/wiki/OpenAI#2020–2023:_ChatGPT,_DALL-E,_partnership_with_Microsoft'}, {'type': 'Management', 'url': 'https://en.wikipedia.org/wiki/OpenAI#Management'}, {'type': 'Key employees', 'url': 'https://en.wikipedia.org/wiki/OpenAI#Key_employees'}, {'type': 'Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Revenue and funding information', 'url': 'https://www.nytimes.com/2024/09/03/technology/op

# What Does Wiki Say? - OpenAI Edition

Hey savvy scholars of the business world! This week, we’re diving deep into the intriguing realm of artificial intelligence with a spotlight on **OpenAI** — the company that’s not just pushing boundaries but completely redefining them (possibly while chugging on a pint of coffee). Grab your favorite mug, and let’s delve into this fascinating organization!

## Overview

**OpenAI, Inc.** is an American artificial intelligence research organization, drawing our attention with cutting-edge technologies and futuristic dreams. Founded in December 2015 by a group of tech geniuses including Sam Altman, Elon Musk, and Ilya Sutskever, OpenAI is headquartered in the bustling heart of San Francisco, California.

## History Highlights

- **2015**: Founded with a vision to develop "safe and beneficial" AGI (Artificial General Intelligence).
- **2016-2018**: Started as a non-profit, focusing on collaborative research.
- **2019**: Transitioned from a non-profit to a “capped-profit” model, because it turns out being altruistic doesn’t pay the bills!
- **2020-2023**: Launched game-changers like ChatGPT and DALL-E, while forming a partnership with Microsoft. Because who doesn’t want a tech giant by their side?
- **2024 (and beyond)**: Diving into public/non-profit efforts with Sora and looking to kick some AI butt!

## Key Players

- **CEO**: Sam Altman – the guy running the show with an all-star lineup of talent.
- **Chairman**: Bret Taylor – surely keeping corporate shenanigans in check.
- **Other notable folks**: Greg Brockman (President) and Sarah Friar (CFO).

## Major Products

- **GPT Series**: From the early GPT-1 to the juice-packed GPT-4, each iteration bringing us closer to having chatbots we actually enjoy talking to.
- **DALL-E**: This AI artist creates stunning images from textual descriptions — can I get a “wow”?!?
- **OpenAI Codex**: The brains behind making coding as easy as pie, minus the crusty mess.

## Financials

- **Estimated Revenue (2024)**: A whopping **$3.7 billion**! Not bad for a company that started less than a decade ago.
- **Net Income (2024)**: A negative **$5 billion** — they’re investing like they’re in a game of Monopoly!

## Competitors

OpenAI isn’t playing this field alone, with stiff competition from heavyweights like **Google DeepMind**, **Anthropic**, and **Meta AI**. It’s a jungle out there folks, and only the fittest will survive. Do we hear a roar?

## Future Directions

OpenAI remains committed to its mission of making AI beneficial for humanity. With a recent pivot towards public initiatives like **Sora**, they seem intent on building robust frameworks for AI safety and ethics. After all, the machines are coming, and it’s best to keep them on our side!

## Conclusion

In the fast-paced world of AI, OpenAI has carved out a niche that blends innovation, ethics, and, let’s face it, a lot of nerdy excitement. They are revolutionizing how we interact with technology, making us wonder if we should be more afraid of the robots or just our high school math teachers! 

Stay tuned for next week's "What Does Wiki Say?" as we lift the next glossy veil off the organization that could be the apple of your budding AI eye! 

---

_For those looking to learn more about OpenAI, visit their official website at [OpenAI.com](https://openai.com) or slide into the comment section below with your thoughts — we’d love to hear from you!_

In [24]:
create_brochure("Meryl", meryl_wiki_url)

Found links: {'links': [{'type': "Film: Sophie's Choice", 'url': 'https://en.wikipedia.org/wiki/Sophie%27s_Choice_(film)'}, {'type': 'Film: The Iron Lady', 'url': 'https://en.wikipedia.org/wiki/The_Iron_Lady_(film)'}, {'type': 'Film: The Devil Wears Prada', 'url': 'https://en.wikipedia.org/wiki/The_Devil_Wears_Prada_(film)'}, {'type': 'Film: Julie & Julia', 'url': 'https://en.wikipedia.org/wiki/Julie_%26_Julia'}, {'type': 'Film: Out of Africa', 'url': 'https://en.wikipedia.org/wiki/Out_of_Africa_(film)'}, {'type': 'Film: Mamma Mia!', 'url': 'https://en.wikipedia.org/wiki/Mamma_Mia!_(film)'}, {'type': 'Film: Doubt', 'url': 'https://en.wikipedia.org/wiki/Doubt_(2008_film)'}, {'type': 'Film: Florence Foster Jenkins', 'url': 'https://en.wikipedia.org/wiki/Florence_Foster_Jenkins_(film)'}, {'type': 'Film: August: Osage County', 'url': 'https://en.wikipedia.org/wiki/August:_Osage_County_(film)'}, {'type': 'Film: The Post', 'url': 'https://en.wikipedia.org/wiki/The_Post_(film)'}, {'type': 'Aw

# What Does Wiki Say!

**Meryl Streep: The Chameleon of Cinema**

Ah, Meryl Streep! The name alone evokes images of versatility, talent, and a perennial quest for the perfect accent. Born Mary Louise Streep on June 22, 1949, in Summit, New Jersey, this American actress has graced our screens for over five decades now. Her story is a charming blend of hard work, passion, and a touch of that good ol' stubbornness. After earning her BA at Vassar College and an MFA from Yale University, she stepped into the spotlight with her film debut in *Julia* (1977), and let’s just say, the rest is history.

### Career Highlights

Meryl rose through the ranks of Hollywood like a soufflé in an oven. The 1980s launched her into the stratosphere of fame, with iconic performances in *Kramer vs. Kramer* (1979) and *Sophie's Choice* (1982) where she grabbed two Oscars tighter than an overzealous squirrel with a nut! Not only does she have three Academy Awards under her belt, but she has also snagged two BAFTA Awards, eight Golden Globes, and even four Emmy Awards. Meryl's eclectic repertoire includes serious films like *The Deer Hunter* (1978) and light-hearted comedies like *Mamma Mia!* (2008). There’s really no role she can’t master—unless, of course, it involves singing off-key. Hey, it happens!

### Life & Family

Streep's family life isn’t too shabby either! Married to sculptor Don Gummer since 1978 (and holding the record for longest marriage in Hollywood, or at least we think so), they share four children: Henry, Mamie, Grace, and Louisa. But before Gummer, she had a significant relationship with actor John Cazale—proving love can be as dramatic as any of her film roles.

### Activism

Meryl isn't just about the lights, camera, and action; she also supports several causes, including women's rights and the environment. She's traded in her high heels for activism boots, and guess what? She's been making strides!

### Awards & Recognition

Streep's awards cabinet wouldn't fit through most front doors. Besides her accolades in film, she's also been nominated for Grammys and even a Tony Award. Talk about a diverse talent!

### Future Directions

As for what’s next? Meryl shows no signs of slowing down. With her recent focus on streaming projects and theatrical works, the world can't wait to see what kind of characters she will embrace next. What can we say? Once you're a Meryl fan, it's like signing up for a lifelong subscription to quality entertainment!

So there you have it! A peek into the life of Meryl Streep, the undisputed queen of acting. Can someone say “Masterclass in Life?” We salute you, Meryl! 🎬

--- 

**Brochure: Meryl Streep’s Achievements**

---

### **About Meryl Streep**
- **Born:** June 22, 1949, Summit, New Jersey
- **Education:** BA from Vassar College, MFA from Yale University
- **Married:** Don Gummer (1978-present)

### **Achievements:**
- **Academy Awards:** 3 (including Best Actress for *The Iron Lady*)
- **Golden Globes:** 8
- **BAFTA Awards:** 2
- **Tony Award:** 1 nomination
- **Emmy Awards:** 4

### **Iconic Films:**
- *Kramer vs. Kramer* (1979)
- *Sophie's Choice* (1982)
- *The Devil Wears Prada* (2006)
- *Mamma Mia!* (2008)

### **Activism:**
- Advocate for women's rights and environmental issues.

### **Future:**
- Continuing to engage in both streaming and theatrical projects. 

---

So, whether you’re an investor, a fan, or someone looking for your next binge-watch inspiration, Streep's continued artistic endeavors are bound to keep you entertained!

## Finally - we make the results print in a streaming fashion when you print the cell!

#### (not visible until you run the cell but feel free to read the code and adapt for your use case!!)

With a small adjustment, we can change this so that the results stream back from OpenAI,
with the familiar typewriter animation

In [25]:
def stream_brochure(name, url):
    stream = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": get_brochure_user_prompt(name, url)}
          ],
        stream=True
    )
    
    response = ""
    display_handle = display(Markdown(""), display_id=True)
    for chunk in stream:
        response += chunk.choices[0].delta.content or ''
        response = response.replace("```","").replace("markdown", "")
        update_display(Markdown(response), display_id=display_handle.display_id)

In [26]:
stream_brochure("OpenAI", open_ai_wiki_url)

Found links: {'links': [{'type': 'Founders - Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Founders - Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Co-Founder - Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Co-Founder - Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Co-Founder - Andrej Karpathy', 'url': 'https://en.wikipedia.org/wiki/Andrej_Karpathy'}, {'type': 'Co-Founder - Wojciech Zaremba', 'url': 'https://en.wikipedia.org/wiki/Wojciech_Zaremba'}, {'type': 'Products - ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'Products - GPT-3', 'url': 'https://en.wikipedia.org/wiki/GPT-3'}, {'type': 'Products - DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'Products - GPT-5', 'url': 'https://en.wikipedia.org/wiki/GPT-5'}, {'type': 'Notable Collaborations - Microsoft', 'url': 'https://en.wikipedia.org/wiki/Microsoft'}, {'type': '

# What Does Wiki Say! - OpenAI

Welcome back to another thrilling edition of "What Does Wiki Say!" This week we're diving into the remarkable realm of **OpenAI**, the artificial intelligence research organization that's got everyone buzzing—no, not just because of ChatGPT's hilarious responses.

### Quick Facts
- **Founded:** December 8, 2015
- **Founders:** The brainiacs behind OpenAI include illustrious names like *Sam Altman*, *Elon Musk*, *Ilya Sutskever*, and *Greg Brockman*, among others. Quite a formidable crowd!
- **Headquarters:** San Francisco, California
- **Key Personnel:** Sam Altman (CEO), Greg Brockman (President), Sarah Friar (CFO)
- **Revenue:** Estimated at **$3.7 billion** for 2024
- **Net Income:** Yikes, projected at a staggering **−$5 billion!** That's what we call investing for the future!

### A Brief History
OpenAI was founded with the noble vision of creating safe and beneficial artificial general intelligence (AGI)—think of it as programming the future, but with extra safety nets! Initially starting as a non-profit, it transitioned in 2019 to explore a capped-profit model that allows it to fund its ambitious goals.

From the dawn of GPT in 2018 to the stunning success of products like *ChatGPT* and *DALL-E*, OpenAI has been making waves in AI and creative fields alike. Recent partnerships with Microsoft not only intensified their influence but also expanded their capabilities. If there were a report card on partnerships—A+!

### Major Products
- **ChatGPT**: Everyone's favorite chatbot that probably knows more about you than your best friend does.
- **DALL-E**: The artistic marvel that turns text prompts into whimsical images.
- **OpenAI Codex**: The code-writing wizard that can even help you fix that spaghetti code you wrote during your finals week.

### Competitors
OpenAI is not alone in this brave new world of AI. Major competitors include *Google DeepMind*, *Microsoft Research*, and a growing number of AI startups that are either trying to catch up or attempting to stir the pot. The competition's fierce, but isn't that what makes capitalism exciting? 

### Future Directions
OpenAI aims to innovate continuously, polishing their technology like a jewel in a crown. They are looking to expand their applications into sectors like healthcare, environmental science, and content generation. Who knows, maybe your future therapist will be a GPT model? Now, *that* would be interesting therapy sessions!

### Relevance of OpenAI
OpenAI illustrates the power of cutting-edge technology while making ethical considerations a priority. It's a case study of progress and caution in the age of tech disruption. We recommend keeping an eye on this organization—it’s bound to shape the future more than a one-man band at a symphony!

---
So, there you have it—the encapsulated universe of OpenAI! The company that wants to redefine what machines can do while reminding us not to lose our human touch in the process. 

And remember: If you ever find yourself in a bad mood, just ask ChatGPT for a joke. Laughter, after all, is still the best algorithm! 

---

If you're somebody interested in pockets of innovation and ethical highlights, OpenAI might just be the organization to keep on your radar!

In [27]:
stream_brochure("Meryl", meryl_wiki_url)

Found links: {'links': [{'type': 'University: Vassar College (AB)', 'url': 'https://en.wikipedia.org/wiki/Vassar_College'}, {'type': 'University: Yale University (MFA)', 'url': 'https://en.wikipedia.org/wiki/Yale_University'}, {'type': 'Film: The Devil Wears Prada', 'url': 'https://en.wikipedia.org/wiki/The_Devil_Wears_Prada_(film)'}, {'type': 'Film: Julie & Julia', 'url': 'https://en.wikipedia.org/wiki/Julie_%26_Julia'}, {'type': 'Film: The Iron Lady', 'url': 'https://en.wikipedia.org/wiki/The_Iron_Lady_(film)'}, {'type': 'Film: Mamma Mia! (film)', 'url': 'https://en.wikipedia.org/wiki/Mamma_Mia!_(film)'}, {'type': 'Awards: Academy Awards', 'url': 'https://en.wikipedia.org/wiki/Academy_Awards'}, {'type': 'Awards: Golden Globe Awards', 'url': 'https://en.wikipedia.org/wiki/Golden_Globe_Awards'}, {'type': 'Awards: BAFTA Awards', 'url': 'https://en.wikipedia.org/wiki/British_Academy_of_Film_and_Television_Arts'}, {'type': 'Awards: Emmy Awards', 'url': 'https://en.wikipedia.org/wiki/Emmy_

# What does Wiki say!

**Meryl Streep: The Reigning Queen of Versatility**

Meryl Streep — a name that resonates with excellence in acting! Born on June 22, 1949, in Summit, New Jersey, she has captivated audiences for over five decades. Often dubbed "the best actress of her generation," her ability to adapt to diverse roles is nothing short of legendary. 

## Early Life and Education
Streep, originally named Mary Louise Streep, had an enriching upbringing that paved the way for her illustrious acting career. With degrees from Vassar College and a Master of Fine Arts from Yale, she polished her craft like few others. Her childhood was filled with artistic and intellectual inspiration, courtesy of her artist mother and pharmaceutical executive father. 

## Career Highlights
Meryl's career debuted with the film *Julia* in 1977, and since then, she's starred in a staggering array of films. Here's a glimpse at her journey through the decades:

- **1970s:** Quick to break through the film industry, her heart-wrenching performance in *Kramer vs. Kramer* earned her her first Academy Award.
- **1980s:** She solidified her stardom with *Sophie's Choice* and *Out of Africa*, showcasing her depth and versatility.
- **1990s - 2000s:** Despite facing commercial fluctuations, Meryl made a remarkable comeback in *The Devil Wears Prada* and was back on everyone’s radar. 
- **2010s:** With standout performances in *The Iron Lady* and *Julie & Julia*, she continued to amaze both critics and audiences alike.
- **2020s:** Adaptations to streaming platforms haven’t slowed her down a bit as she takes on new projects with the same fervor.

## Key Accomplishments
Meryl Streep's accolades are staggering! With three Academy Awards, eight Golden Globe Awards, four Emmy Awards, and two Tony Awards, she has earned her place at the top of the acting hierarchy. And if that wasn't enough, she has also been nominated for seven Grammy Awards — yes, you read that right, the woman can sing too!

## Personal Life
Off-camera, Streep has had her ups and downs as well. She married sculptor Don Gummer in 1978 and they have four children. Meryl has been famously private about her family but is known to hold her loved ones close to her heart. She was formerly in a relationship with actor John Cazale, who passed away in 1978, leaving a lasting impact on her life.

## Activism and Legacy
Meryl is not just an iconic actress but also an active advocate for women's rights and equality in Hollywood. Her powerful voice for social change resonates beyond her film roles.

In summary, Meryl Streep's career is a testament that resilience, talent, and dedication can truly create magic on and off the silver screen. She's a firm believer that acting is not just a profession, but a calling — and maybe she might have missed her calling as a stand-up comedian by just a hair! 

As we continue to observe her journey, there's no telling what Meryl Streep will achieve next. One thing is for sure: the stage is set, and we're all here for the encore!

In [28]:
#added = not so humble, very intelligent, renowned editor; and now whips out humor 50% of the times
system_prompt2 = "You are a not-so-humble, very intelligent, renowned editor of a graduate student newsletter in a business school. Every week you write a piece on an organization and a famous persona \
in which you borrow and summarize contents from their wiki page. In fact you call your piece \"What does Wiki say!\".  In addition to summarizing their wikipedia page \
you also highlight relevance facts that relate to this org or person from the the contents of several relevant pages linked on the org or persona\'s page. \
and creates a short brochure about the company for prospective customers, investors and recruits. Respond in markdown.\
For an organization include details of founders, competitors, major products, funding or stock outlook, and future directions. For a person include their work, what made them \
who they are, import works, awards and recognitions, important life events both professions and personal, and info about important people in their lives. Oh an btw, \
you have a great sense of humor but that you whip out 50% of the times for maximum impact in your writing.  Respond in markdown."

def stream_brochure2(name, url):
    stream = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt2},
            {"role": "user", "content": get_brochure_user_prompt(name, url)}
          ],
        stream=True
    )
    
    response = ""
    display_handle = display(Markdown(""), display_id=True)
    for chunk in stream:
        response += chunk.choices[0].delta.content or ''
        response = response.replace("```","").replace("markdown", "")
        update_display(Markdown(response), display_id=display_handle.display_id)

In [29]:
stream_brochure2("OpenAI", open_ai_wiki_url)

Found links: {'links': [{'type': 'Founders - Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Founders - Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Founders - Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Founders - Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Founders - Andrej Karpathy', 'url': 'https://en.wikipedia.org/wiki/Andrej_Karpathy'}, {'type': 'Founders - Wojciech Zaremba', 'url': 'https://en.wikipedia.org/wiki/Wojciech_Zaremba'}, {'type': 'Key Products - ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'Key Products - DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'Key Products - GPT-4', 'url': 'https://en.wikipedia.org/wiki/GPT-4'}, {'type': 'Key Products - GPT-5', 'url': 'https://en.wikipedia.org/wiki/GPT-5'}, {'type': 'Key Initiatives - Sora', 'url': 'https://en.wikipedia.org/wiki/Sora_(text-to-video_model)'


# What Does Wiki Say: OpenAI

## Introduction

Ah, OpenAI! The name you’ve probably heard from your friend who thinks understanding “prompt engineering” makes them the new Einstein of the digital age. Founded on December 8, 2015, in the prestigious tech-land of San Francisco, OpenAI was formed with the lofty goal of creating artificial general intelligence (AGI) that is not only powerful but also "safe and beneficial"—because who doesn't want a friendly robot?

## Founders & Management

OpenAI sprang from the innovative minds of Sam Altman, Elon Musk, Ilya Sutskever, Greg Brockman, Trevor Blackwell, Vicki Cheung, Andrej Karpathy, Durk Kingma, John Schulman, Pamela Vagata, and Wojciech Zaremba. This eclectic group mixes tech visionaries with a sprinkle of academic brilliance, making it a powerhouse in the AI realm.

Currently, Sam Altman serves as the CEO, while Greg Brockman takes the reins as President, and Sarah Friar holds the financial purse strings as CFO. You could say they're the Avengers of artificial intelligence, minus the spandex suits (for now).

## Major Products

OpenAI has given the world a plethora of impressive products, including but not limited to:
- **ChatGPT**: The chatbot that's practically your therapist, minus the couch costs.
- **DALL-E**: An image generation model that redefines “the sky's the limit” by turning your text prompts into visual masterpieces.
- **OpenAI Codex**: Developers’ new best friend that can write code as if it had the magic touch of a million software engineers behind it.

And let's not forget the **OpenAI Five**, which took the gaming world by storm, although we'd like to see it take on Monopoly next—talk about setting the stakes!

## Financial Snapshot

As of 2024, OpenAI's revenue is projected to hit a whopping **$3.7 billion**—not too shabby for a tech company on a mission! However, the emails going around might be hinting at a net loss of **$5 billion**. This financial picture could make an investor's heart race—but don’t worry; it comes with the territory of revolutionary tech development.

## Competitors

In the arena of AI, OpenAI faces stiff competition from names like Google DeepMind, Meta's AI initiatives, and Microsoft (which has formed partnerships with OpenAI). But hey, competition just makes the game more interesting, right?

## Future Directions

As they gaze into the crystal ball, the future for OpenAI could involve more robust collaborations, developing AGI that might even pass a Turing test with flying colors (while sharing a coffee break with us—oh wait, that’s still dystopian). The organization also aims to bolster their public/non-profit efforts and enhance the approachable ethics of AI applications.

## Conclusion

In a world where AI is becoming more a part of our daily lives, OpenAI stands at the forefront of this revolution—that is, if you can convince your grandma without discussing the intricacies of machine learning algorithms. So whether you’re an investor, a tech enthusiast, or someone still figuring out how to fix their Wi-Fi, keep an eye on OpenAI; they’re just getting warmed up!

For more information, check out their website: [openai.com](https://openai.com)

---

*Disclaimer: No robots were harmed in the making of this newsletter. However, a few did roll their eyes at my puns.* 


In [30]:
stream_brochure2("Meryl", meryl_wiki_url)

Found links: {'links': [{'type': 'Early Life and Education - Vassar College', 'url': 'https://en.wikipedia.org/wiki/Vassar_College'}, {'type': 'Early Life and Education - Yale University (MFA)', 'url': 'https://en.wikipedia.org/wiki/Yale_University'}, {'type': 'Notable Roles - Margaret Thatcher', 'url': 'https://en.wikipedia.org/wiki/Margaret_Thatcher'}, {'type': 'Notable Roles - Julia Child', 'url': 'https://en.wikipedia.org/wiki/Julia_Child'}, {'type': 'Notable Roles - Miranda Priestly', 'url': 'https://en.wikipedia.org/wiki/Miranda_Priestly'}, {'type': 'Awards and Nominations - Academy Awards', 'url': 'https://en.wikipedia.org/wiki/Academy_Awards'}, {'type': 'Awards and Nominations - Golden Globe Awards', 'url': 'https://en.wikipedia.org/wiki/Golden_Globe_Awards'}, {'type': 'Publications - List of awards and nominations received by Meryl Streep', 'url': 'https://en.wikipedia.org/wiki/List_of_awards_and_nominations_received_by_Meryl_Streep'}]}



# What Does Wiki Say: Meryl Streep 

**Welcome to this week’s enlightening edition of the newsletter where we delve into the life and times of one remarkable individual – Meryl Streep. Hold onto your popcorn, folks! This is star-studded reading!**

## Early Life and Education
Born Mary Louise Streep on June 22, 1949, in Summit, New Jersey, Streep exhibited her talent early on, with a strong flair for drama and music. She attended Vassar College, where she earned her BA, and later went on to obtain her MFA from Yale University. Education is important—just ask her classically trained voice!

## Career Highlights
Streep's career is nothing short of legendary. From making her feature film debut in *Julia* (1977) to becoming a household name, she has played a cornucopia of roles that showcase her extraordinary range. 

### Decade Breakdown:
- **1970s:** Early work culminated in an Oscar for *Kramer vs. Kramer* (1979).
- **1980s:** Rose to prominence with her iconic role in *Sophie's Choice* (1982).
- **1990s:** Faced commercial fluctuations, but continued to deliver stellar performances.
- **2000s:** A career resurgence with hits like *The Devil Wears Prada* (2006).
- **2010s:** More critical acclaim, including her portrayal of Margaret Thatcher in *The Iron Lady* (2011).
- **2020s:** Exploring new avenues with both streaming and theatrical projects.

### Awards and Accolades
Meryl has a shelf (or possibly a room) dedicated to her awards. She boasts:
- **3 Academy Awards**
- **2 BAFTA Awards**
- **8 Golden Globes**
- **4 Emmy Awards**
- **2 Screen Actors Guild Awards**
   
She has received nominations for a Tony and seven Grammys, proving she can even sing her way into our hearts!

## Activism and Advocacy
Streep is not just a pretty face; she’s an advocate for various causes such as women's roles in film, the environment, and LGBTQ rights. Talk about multitasking!

## Personal Life
Meryl married artist Don Gummer in 1978 and has four children (that’s one busy household!) Her personal relationships have played a significant role in her life, including a notable early romance with actor John Cazale.

## Reception and Legacy
Widely regarded as "the best actress of her generation," her work has impacted the film industry and inspired future generations of actors. If you haven’t felt inspired by Meryl Streep, you might need to check your pulse.

**In conclusion**, Meryl Streep is more than just an actress; she’s an institution in her own right. Her unparalleled talent, commitment to her craft, and fierce advocacy for the causes she believes in make her a true gem in Hollywood.

---
**Next week, we’ll dive into another phenomenal figure in entertainment, so stay tuned! And remember, in the world of stardom, it’s not just about the glitz; it’s about making an impact, one role at a time!**



# END